## Data parsing from MongoDB

In [1]:
import pandas as pd
from pymongo import MongoClient
from datetime import datetime
client = MongoClient('52.79.241.214', 27017)
print("DB connection complete!!")

DB connection complete!!


In [2]:
DB_Coin = client.Coin
Posts = DB_Coin.posts

In [3]:
import time
DB_schema = []
i = 0

"""
Data Dimension (200,5)

"""
for post in Posts.find({}):
    if i==200:
        continue
    temp_record = {}

    temp_record['open'] = post['price_open']
    temp_record['close'] = post['price_close']
    temp_record['high'] = post['price_high']
    temp_record['low'] = post['price_low']
    temp_record['volume'] = post['volume_traded']    
    DB_schema.append(temp_record)
    del temp_record
    i = i + 1

## Making Tensorflow graph

In [4]:
# 절대 임포트 설정
from __future__ import division, print_function, absolute_import

# 필요한 라이브러리들을 임포트
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
from tensorflow.contrib import rnn

%matplotlib inline

In [5]:
"""
define all the constants
"""
numEpochs = 100
seriesLength = 200
stateSize = 4
numClasses = 50
echoStep = 3
batchSize = 10
backpropagationLength = batchSize
num_batches = seriesLength // batchSize // backpropagationLength
print("Batch numbers : ", num_batches)

param_sparsity = 0.01
param_weight_decay = 0.0001
param_sparse_panelty = 3

learning_rate_Gradient_Descent = 0.005
softmax_classifier_iterations = 1000 # Softmax Classifier iteration 횟수 
  
display_step = 1        # 몇 Step마다 log를 출력할지 결정한다.
examples_to_show = 10   # reconstruct된 이미지 중 몇개를 보여줄지를 결정한다. 

Batch numbers :  2


In [6]:

def generateData(raw_input):
    #x = np.array(np.random.choice(25, seriesLength, p=[0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04]))
    #x = np.random.random((5, 200))
    x = raw_input
    y = np.roll(x, echoStep)
    y[0:echoStep] = 0
    
    print("x :", x.shape)
    print("y :", y.shape)
    print("batchSize : ", batchSize)

    x = x.reshape((batchSize, -1))
    y = y.reshape((batchSize, -1))
    
    print("x_reshape :", x.shape)
    print("y_reshape :", y.shape)

    return (x, y)

In [7]:
def regularization(weights):
    return tf.nn.l2_loss(weights)

def Single_Layer_Autoencoder(Input_Layer, n_input, n_hidden):
    with tf.name_scope("Hidden_Layer") as scope:
        # 히든 레이어 1을 위한 Weights와 Biases
        W_ih = tf.Variable(tf.random_normal([n_input, n_hidden]), name = "Weight_IH")  # IH = Input_Hidden
        b_ih = tf.Variable(tf.random_normal([n_hidden]), name = "Bias_IH")
        H_Layer = tf.nn.sigmoid(tf.matmul(Input_Layer, W_ih) + b_ih, name = "Hidden")     # 히든레이어 1의 activation (sigmoid 함수를 사용)
               
    with tf.name_scope("Reconstructed_Layer") as scope:
        # Output 레이어를 위한 Weights와 Biases
        W_hr = tf.Variable(tf.random_normal([n_hidden, n_input]), name = "Weight_HR")  # HR = Hidden_Reconstructed
        b_hr = tf.Variable(tf.random_normal([n_input]), name = "Bias_HR")
        X_reconstructed = tf.nn.sigmoid(tf.matmul(H_Layer,W_hr) + b_hr, name = "Hidden_HR")   # Output 레이어의 activation (sigmoid 함수를 사용)
    
    with tf.name_scope("cost") as scope:        
    # Autoencoder Optimization을 위한 파라미터들
        average_act_hidden = tf.reduce_mean(H_Layer,axis=0)   #Average hidden layer over all data points in X, Page 14 in https://web.stanford.edu/class/cs294a/sparseAutoencoder_2011new.pdf
        diff = Input_Layer - X_reconstructed
        KL = Kullback_Leibler_divergence(rho, average_act_hidden)
        cost= 0.5*tf.reduce_mean(tf.reduce_sum(tf.pow(diff,2),axis=1)) + 0.5*Lambda*(tf.nn.l2_loss(W_ih) + tf.nn.l2_loss(W_hr)) + Beta*tf.reduce_sum(KL)
        cost_summary = tf.summary.scalar("cost", cost)
        

    return H_Layer, X_reconstructed, cost

def Kullback_Leibler_divergence(rho, rho_hat):
    return rho * tf.log(rho) - rho * tf.log(rho_hat) + (1 - rho) * tf.log(1 - rho) - (1 - rho) * tf.log(1 - rho_hat)

In [8]:
rho = param_sparsity
Lambda = param_weight_decay
Beta = param_sparse_panelty

# 학습에 필요한 변수들 설정
with tf.name_scope("Tensor_initialize"):
       
    batchXHolder = tf.placeholder(tf.float32, [batchSize, backpropagationLength], name="x_input")
    batchYHolder = tf.placeholder(tf.int32, [batchSize, backpropagationLength], name="y_input")    
        
with tf.name_scope("Auto_Encoder_01"):
    H1, O1, cost1 = Single_Layer_Autoencoder(batchXHolder, batchSize, batchSize)
    optmzr1 = tf.train.GradientDescentOptimizer(learning_rate_Gradient_Descent).minimize(cost1)

with tf.name_scope("Auto_Encoder_02"):
    H2, O2, cost2 = Single_Layer_Autoencoder(H1, batchSize, batchSize)
    optmzr2 = tf.train.GradientDescentOptimizer(learning_rate_Gradient_Descent).minimize(cost2)

with tf.name_scope("Auto_Encoder_03"):
    H3, O3, cost3 = Single_Layer_Autoencoder(H2, batchSize, batchSize)
    optmzr3 = tf.train.GradientDescentOptimizer(learning_rate_Gradient_Descent).minimize(cost3)

with tf.name_scope("Auto_Encoder_04"):
    H4, O4, cost4 = Single_Layer_Autoencoder(H3, batchSize, batchSize)
    optmzr4 = tf.train.GradientDescentOptimizer(learning_rate_Gradient_Descent).minimize(cost4)

with tf.name_scope("Long_Short_Memory_Networks"):
    cellState = tf.placeholder(tf.float32, [batchSize, stateSize])
    hiddenState = tf.placeholder(tf.float32, [batchSize, stateSize])
    initState = rnn.LSTMStateTuple(cellState, hiddenState)
    
    W = tf.Variable(np.random.rand(stateSize+1, stateSize), dtype=tf.float32, name="weight1")
    bias1 = tf.Variable(np.zeros((1,stateSize)), dtype=tf.float32)
    W2 = tf.Variable(np.random.rand(stateSize, numClasses),dtype=tf.float32, name="weight2")
    bias2 = tf.Variable(np.zeros((1,numClasses)), dtype=tf.float32)
    
    tf.summary.histogram(name="LSTM_weights", values=W)
        
    # Unpack columns
    inputsSeries = tf.split(axis=1, num_or_size_splits=backpropagationLength, value=H4)
    labelsSeries = tf.unstack(batchYHolder, axis=1)
        
    # Forward passes
    cell = rnn.BasicLSTMCell(stateSize, state_is_tuple=True)
    statesSeries, currentState = rnn.static_rnn(cell, inputsSeries, initState)
    
    # calculate loss
    logits_series = [tf.matmul(state, W2) + bias2 for state in statesSeries]
    print("logits_series :",len(logits_series))
    predictions_series = [tf.nn.softmax(logits) for logits in logits_series]
    print("predictions_series :", len(predictions_series))
    losses = [tf.nn.sparse_softmax_cross_entropy_with_logits(labels=labels, logits=logits) for logits, labels in zip(logits_series,labelsSeries)]
    total_loss = tf.reduce_mean(losses, name="total_loss")
    train_step = tf.train.AdagradOptimizer(0.3).minimize(total_loss, name="training")

logits_series : 10
predictions_series : 10


In [ ]:
"""
plot computation
"""
def plot(loss_list, predictions_series, batchX, batchY):
    plt.subplot(2, 3, 1)
    plt.cla()
    plt.plot(loss_list)

    for batchSeriesIdx in range(5):
        oneHotOutputSeries = np.array(predictions_series)[:, batchSeriesIdx, :]
        singleOutputSeries = np.array([(1 if out[0] < 0.5 else 0) for out in oneHotOutputSeries])

        plt.subplot(2, 3, batchSeriesIdx + 2)
        plt.cla()
        plt.axis([0, backpropagationLength, 0, 2])
        left_offset = range(backpropagationLength)
        plt.bar(left_offset, batchX[batchSeriesIdx, :], width=1, color="blue")
        plt.bar(left_offset, batchY[batchSeriesIdx, :] * 0.5, width=1, color="red")
        plt.bar(left_offset, singleOutputSeries * 0.3, width=1, color="green")

    plt.draw()    

## Execution

In [9]:
from tqdm import tqdm_notebook
from pywt import wavedec, waverec

"""
run the graph
"""
with tf.Session() as sess:
    writer = tf.summary.FileWriter("./logs/SAE_test8", graph=tf.get_default_graph())
    writer.add_graph(sess.graph)
    sess.run(tf.global_variables_initializer())
    #plt.ion()
    #plt.figure()
    #plt.show()
    loss_list = []

    for epoch_idx in range(numEpochs):
        DF = pd.DataFrame(DB_schema) # DataFrame
        inputData = DF.values # ndarray
        print("input shape : ", inputData.shape)
        del DF
        x,y = generateData(inputData)  
        _current_cell_state = np.zeros((batchSize, stateSize))
        _current_hidden_state = np.zeros((batchSize, stateSize))

        print("New data, epoch", epoch_idx)

        for batch_idx in range(num_batches):
            start_idx = batch_idx * backpropagationLength
            end_idx = start_idx + backpropagationLength
            print('batch idx : ', batch_idx)
            print('start idx : ', start_idx)
            print('end idx : ', end_idx)

            batchX = x[:,start_idx:end_idx]            
            batchY = y[:,start_idx:end_idx]
            
            print("batchX : ", batchX.shape)
            print("batchY : ", batchY.shape)
            
            if batchX.shape[1] != backpropagationLength:
                continue
            
            coeffs = wavedec(batchX, 'haar', level=2)
            reconstruct_X = waverec(coeffs, 'haar')
            
            #_, SAE_cost1 = sess.run([optmzr1, cost1], feed_dict={batchXHolder: reconstruct_X, batchYHolder: batchY})
            #_, SAE_cost2 = sess.run([optmzr2, cost2], feed_dict={batchXHolder: reconstruct_X, batchYHolder: batchY})
            #_, SAE_cost3 = sess.run([optmzr3, cost3], feed_dict={batchXHolder: reconstruct_X, batchYHolder: batchY})
            #_, SAE_cost4 = sess.run([optmzr4, cost4], feed_dict={batchXHolder: reconstruct_X, batchYHolder: batchY}) 

            _total_loss, _train_step, _current_state, _predictions_series = sess.run(
                [total_loss, train_step, currentState, predictions_series],
                feed_dict={
                    batchXHolder:reconstruct_X,
                    batchYHolder:batchY,
                    cellState: _current_cell_state,
                    hiddenState: _current_hidden_state
                })

            _current_cell_state, _current_hidden_state = _current_state
            print("predictions series : ", _predictions_series )

            loss_list.append(_total_loss)

            # fix the cost summary later
            tf.summary.scalar(name="totalloss", tensor=_total_loss)

            print("Batch index",batch_idx, "Loss", _total_loss)
            #plot(loss_list, _predictions_series, batchX, batchY)

#plt.ioff()
#plt.show()

input shape :  (200, 5)
x : (200, 5)
y : (200, 5)
batchSize :  10
x_reshape : (10, 100)
y_reshape : (10, 100)
New data, epoch 0
batch idx :  0
start idx :  0
end idx :  10
batchX :  (10, 10)
batchY :  (10, 10)
predictions series :  [array([[0.020041  , 0.01992948, 0.02008879, 0.01987531, 0.0199297 ,
        0.01994012, 0.01989732, 0.0199348 , 0.02010019, 0.01994041,
        0.02007004, 0.01992069, 0.02017877, 0.02003112, 0.0199765 ,
        0.02008746, 0.02007472, 0.02000091, 0.0198297 , 0.0200955 ,
        0.0200317 , 0.02000102, 0.01998179, 0.01993997, 0.01999079,
        0.01997194, 0.0200143 , 0.02012734, 0.02016082, 0.02011064,
        0.0199791 , 0.02001369, 0.02012878, 0.02001332, 0.0198948 ,
        0.01990229, 0.02007862, 0.01990555, 0.02002479, 0.01991211,
        0.01984133, 0.02005773, 0.02017294, 0.02014866, 0.01996528,
        0.0201773 , 0.01985976, 0.01993037, 0.01990558, 0.01981498],
       [0.020041  , 0.01992948, 0.02008879, 0.01987531, 0.0199297 ,
        0.01994012

      dtype=float32)]
Batch index 0 Loss nan
batch idx :  1
start idx :  10
end idx :  20
batchX :  (10, 10)
batchY :  (10, 10)
predictions series :  [array([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],


      dtype=float32)]
Batch index 1 Loss nan
input shape :  (200, 5)
x : (200, 5)
y : (200, 5)
batchSize :  10
x_reshape : (10, 100)
y_reshape : (10, 100)
New data, epoch 1
batch idx :  0
start idx :  0
end idx :  10
batchX :  (10, 10)
batchY :  (10, 10)
predictions series :  [array([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        na

      dtype=float32)]
Batch index 0 Loss nan
batch idx :  1
start idx :  10
end idx :  20
batchX :  (10, 10)
batchY :  (10, 10)
predictions series :  [array([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],


      dtype=float32)]
Batch index 1 Loss nan
input shape :  (200, 5)
x : (200, 5)
y : (200, 5)
batchSize :  10
x_reshape : (10, 100)
y_reshape : (10, 100)
New data, epoch 2
batch idx :  0
start idx :  0
end idx :  10
batchX :  (10, 10)
batchY :  (10, 10)
predictions series :  [array([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        na

...

      dtype=float32)]
Batch index 1 Loss nan
input shape :  (200, 5)
x : (200, 5)
y : (200, 5)
batchSize :  10
x_reshape : (10, 100)
y_reshape : (10, 100)
New data, epoch 98
batch idx :  0
start idx :  0
end idx :  10
batchX :  (10, 10)
batchY :  (10, 10)
predictions series :  [array([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        n

      dtype=float32)]
Batch index 0 Loss nan
batch idx :  1
start idx :  10
end idx :  20
batchX :  (10, 10)
batchY :  (10, 10)
predictions series :  [array([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],


      dtype=float32)]
Batch index 1 Loss nan
input shape :  (200, 5)
x : (200, 5)
y : (200, 5)
batchSize :  10
x_reshape : (10, 100)
y_reshape : (10, 100)
New data, epoch 99
batch idx :  0
start idx :  0
end idx :  10
batchX :  (10, 10)
batchY :  (10, 10)
predictions series :  [array([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        n

      dtype=float32)]
Batch index 0 Loss nan
batch idx :  1
start idx :  10
end idx :  20
batchX :  (10, 10)
batchY :  (10, 10)
predictions series :  [array([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],
       [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
        nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan],


      dtype=float32)]
Batch index 1 Loss nan
